# Hafta 4: MLOps Prensipleri ve Deney Yönetimi

**Dersin Hedefleri:**
1.  MLOps'un ne olduğunu ve geleneksel DevOps'tan neden farklı olduğunu anlamak.
2.  Makine öğrenmesi yaşam döngüsünün (ML Lifecycle) ana aşamalarını tanımak.
3.  Deney yönetiminin (Experiment Tracking) neden bir lüks değil, bilimsel titizlik için bir zorunluluk olduğunu kavramak.
4.  `MLflow` kütüphanesini kullanarak deney parametrelerini, metrikleri ve model dosyalarını (artifacts) kaydetmek.
5.  Farklı deney sonuçlarını karşılaştırarak en iyi modeli seçmek.

## 1. MLOps Nedir?

**MLOps (Machine Learning Operations)**, makine öğrenmesi modellerini güvenilir ve verimli bir şekilde üretime almak, dağıtmak ve sürdürmek için gereken pratikler, prensipler ve kültür bütünüdür.

**MLOps != DevOps:**
Geleneksel yazılım (DevOps) sadece **koda** odaklanır. MLOps ise üç hareketli parçayı yönetmek zorundadır:

1.  **Kod (Code):** Veri işleme, eğitim, tahmin vb. için yazılan script'ler.
2.  **Model (Model):** Eğitim süreci sonunda ortaya çıkan ve versiyonlanması gereken dosya (artifact).
3.  **Veri (Data):** Modelin performansını doğrudan etkileyen ve sürekli değişebilen girdi.

Bu üçlü yapı, ML sistemlerini daha karmaşık ve dinamik hale getirir.

## 2. Deney Yönetimi: Kaostan Düzene

Bir veri bilimci olarak sürekli şu sorularla karşılaşırsınız:
- *En iyi sonucu veren modeli hangi hiperparametrelerle eğitmiştim?*
- *Bu model, veri setinin hangi versiyonuyla eğitildi?*
- *İki hafta önce yaptığım denemenin sonuçlarını şimdikilerle nasıl adil bir şekilde karşılaştırabilirim?*

Bu sorulara cevap veremiyorsanız, yaptığınız iş tekrarlanabilir değildir. Deney yönetimi, bu soruların cevabını sistematik olarak kaydetme sürecidir.

**Ne Kaydedilir?**
- **Parametreler:** Modelin hiperparametreleri (örn: `n_estimators`, `learning_rate`), özellik mühendisliği adımları.
- **Metrikler:** Modelin performansını ölçen değerler (örn: `accuracy`, `f1-score`, `roc_auc`).
- **Artifacts (Çıktılar):** Eğitilmiş model dosyası (`model.pkl`), görselleştirmeler (`confusion_matrix.png`), özellik önem sıralaması (`features.csv`).
- **Kaynak Kod:** Deneyi çalıştıran kodun `git` commit hash'i.

## 3. `MLflow` ile Pratik Uygulama

`MLflow`, deney yönetimi için açık kaynaklı bir standarttır.

**Kurulum:**
```bash
pip install mlflow
```

**Temel Bileşenler:**
- **MLflow Tracking:** Parametreleri, metrikleri ve artifact'leri kaydetmek için kullanılan API.
- **MLflow UI:** Deney sonuçlarını görsel olarak incelemek ve karşılaştırmak için web tabanlı bir arayüz. Terminalden `mlflow ui` komutu ile başlatılır.

### Uygulama: Churn Modeli Deneylerini Yönetme

Önceki haftadan gelen `customer_df` verisini kullanarak bir churn tahmin modeli eğiteceğiz ve farklı parametrelerle yaptığımız denemeleri `MLflow` ile kaydedeceğiz.

In [ ]:
import pandas as pd
import numpy as np
import mlflow
from datetime import datetime, timedelta
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, f1_score, roc_auc_score
import warnings

# Uyarı mesajlarını gizleme (temiz çıktı için)
warnings.filterwarnings("ignore")

## Adım 2: Veri Hazırlama Fonksiyonu

Bu fonksiyon, önceki haftalarda öğrendiğimiz veri ön işleme adımlarını kapsüller. Fonksiyonun amacı:

1. **Tekrarlanabilirlik**: Aynı veri üretim sürecini her çalıştırmada tutarlı şekilde uygulamak
2. **Modülerlik**: Veri hazırlama kodunu ana deney akışından ayırarak kod okunabilirliğini artırmak
3. **Esneklik**: Farklı boyutlarda veri setleri oluşturabilme imkanı sağlamak

Fonksiyon içinde gerçekleştirilen işlemler:
- Sentetik müşteri verisi oluşturma (demographics, behavior, target)
- Eksik değer analizi ve doldurma (imputation)
- Kategorik değişken kodlama (one-hot encoding)
- Zaman tabanlı özellik çıkarımı (feature engineering)

In [ ]:
# Veri hazırlama fonksiyonu (Hafta 3'ten)
def get_prepared_data(num_customers=500):
    """
    Churn prediction için sentetik müşteri verisi oluşturur ve hazırlar.
    
    Adımlar:
    1. Sentetik veri oluşturma
    2. Eksik değerleri doldurma (Imputation)
    3. Kategorik değişkenleri kodlama (Encoding)
    4. Tarih özelliklerini çıkarma (Feature extraction)
    """
    np.random.seed(42)
    
    # 1. Sentetik veri oluşturma
    customer_ids = range(1, num_customers + 1)
    ages = np.random.randint(18, 70, size=num_customers)
    ages = [age if np.random.rand() > 0.1 else np.nan for age in ages]
    cities = np.random.choice(['Istanbul', 'Ankara', 'Izmir'], size=num_customers, p=[0.5, 0.3, 0.2])
    end_date = datetime.now()
    start_date = end_date - timedelta(days=3*365)
    registration_dates = [start_date + timedelta(seconds=np.random.randint(0, int((end_date - start_date).total_seconds()))) for _ in range(num_customers)]
    total_spent = np.random.gamma(2, 150, size=num_customers).round(2)
    total_spent += np.array([age * 1.5 if not np.isnan(age) else 0 for age in ages])
    last_seen_days_ago = np.random.randint(0, 365, size=num_customers)
    last_seen_days_ago = [d if np.random.rand() > 0.15 else np.nan for d in last_seen_days_ago]
    churn_probability = 1 / (1 + np.exp(-( (np.array(last_seen_days_ago, dtype=float) / 300) - (total_spent / 600) )))
    churn = (np.random.rand(num_customers) < churn_probability).astype(int)
    
    df = pd.DataFrame({
        'customer_id': customer_ids, 
        'age': ages, 
        'city': cities, 
        'registration_date': registration_dates, 
        'total_spent': total_spent, 
        'last_seen_days_ago': last_seen_days_ago, 
        'churn': churn
    })
    
    # 2. Eksik değerleri doldurma (Imputation)
    df['age'].fillna(df['age'].median(), inplace=True)
    df['last_seen_days_ago'].fillna(df['last_seen_days_ago'].median(), inplace=True)
    
    # 3. Kategorik değişkenleri kodlama (One-hot encoding)
    city_dummies = pd.get_dummies(df['city'], prefix='city', drop_first=True)
    df = pd.concat([df, city_dummies], axis=1)
    df.drop('city', axis=1, inplace=True)

    # 4. Tarih özelliklerini çıkarma
    df['registration_date'] = pd.to_datetime(df['registration_date'])
    df['membership_days'] = (datetime.now() - df['registration_date']).dt.days
    df.drop('registration_date', axis=1, inplace=True)
    
    return df

print("✓ Veri hazırlama fonksiyonu tanımlandı")

## Adım 3: Veri Yükleme ve Train/Test Ayırma

Bu adımda veri seti oluşturulur ve makine öğrenmesi modellemesi için uygun formata dönüştürülür.

**Stratified Split Kullanımı:**
- `stratify=y` parametresi, hedef değişkenin (churn) dağılımının hem eğitim hem de test setinde orantılı şekilde korunmasını sağlar
- Bu yaklaşım, özellikle dengesiz sınıf dağılımlarında modelin performansının daha güvenilir değerlendirilmesini mümkün kılar

**Test Seti Oranı:**
- %20 test verisi, genellikle yeterli değerlendirme gücü sağlarken eğitim için yeterli veri bırakır
- Daha küçük veri setlerinde bu oran artırılabilir (örn: %30), büyük veri setlerinde azaltılabilir (örn: %10)

In [ ]:
# Veriyi hazırlama
customer_df = get_prepared_data()

# Özellikler (X) ve hedef değişken (y) ayırma
X = customer_df.drop(['churn', 'customer_id'], axis=1)
y = customer_df['churn']

# Train/Test split
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, random_state=42, stratify=y
)

print(f"✓ Veri hazırlandı: {len(customer_df)} müşteri")
print(f"  - Eğitim seti: {len(X_train)} örnek")
print(f"  - Test seti: {len(X_test)} örnek")
print(f"  - Özellik sayısı: {X.shape[1]}")
print(f"\nÖzellikler: {list(X.columns)}")

## Adım 4: MLflow Deneyini Başlatma

**Deney (Experiment) Kavramı:**

MLflow'da bir "experiment" (deney), belirli bir problemi çözmek için yapılan tüm denemelerin (runs) mantıksal olarak gruplandığı bir konteynerdir. 

**Deney Organizasyonu:**
- Her proje için ayrı bir deney oluşturmak, sonuçların daha kolay yönetilmesini sağlar
- Deney adları açıklayıcı olmalıdır (örn: "Churn Prediction Experiments", "Customer Segmentation v2")
- Aynı deney altındaki tüm çalıştırmalar karşılaştırılabilir ve sıralanabilir

**MLflow Tracking Serveri:**
- Tüm deney verileri yerel olarak `mlruns/` dizininde saklanır
- Her deneme için benzersiz bir ID oluşturulur
- Parametreler, metrikler ve artifactlar otomatik olarak sürümlenir

In [ ]:
# MLflow deneyini ayarlama
mlflow.set_experiment("Churn Prediction Experiments")

print("✓ MLflow deneyi başlatıldı: 'Churn Prediction Experiments'")

## Adım 5: Deney 1 - Logistic Regression

**Model Seçimi: Logistic Regression**

Logistic Regression, ikili sınıflandırma problemleri için temel bir başlangıç noktasıdır. Avantajları:
- Hesaplama açısından verimli
- İyi yorumlanabilirlik (katsayılar değişken etkilerini gösterir)
- Doğrusal ayırılabilir problemlerde yüksek performans
- Overfitting riski düşük

**MLflow İş Akışı:**

Bir MLflow denemesi beş temel adımdan oluşur:

1. **Run Başlatma**: `mlflow.start_run()` ile yeni bir deneme başlatılır
2. **Parametre Kaydetme**: `mlflow.log_param()` ile hiperparametreler kaydedilir
3. **Model Eğitimi**: Standart scikit-learn API kullanılır
4. **Metrik Kaydetme**: `mlflow.log_metric()` ile performans metrikleri kaydedilir
5. **Model Kaydetme**: `mlflow.sklearn.log_model()` ile eğitilmiş model artifact olarak saklanır

**Metrik Seçimi:**
- **Accuracy**: Genel doğruluk oranı (dengeli veri setleri için uygundur)
- **F1-Score**: Precision ve recall'un harmonik ortalaması (dengesiz sınıflarda tercih edilir)
- **ROC-AUC**: Model ayrım gücünün olasılık eşiklerinden bağımsız ölçüsü

In [ ]:
with mlflow.start_run(run_name="Logistic Regression"):
    print("🔄 Çalışan Deney: Logistic Regression")
    
    # 1. Hiperparametreleri MLflow'a kaydetme
    # Bu parametreler daha sonra deney karşılaştırmalarında kullanılabilir
    mlflow.log_param("model_type", "LogisticRegression")
    mlflow.log_param("max_iter", 1000)
    mlflow.log_param("solver", "lbfgs")  # Default solver
    
    # 2. Model eğitimi
    # random_state: Tekrarlanabilirlik için sabit tohum değeri
    model = LogisticRegression(max_iter=1000, random_state=42)
    model.fit(X_train, y_train)
    
    # 3. Tahminlerin hesaplanması
    # y_pred: Sınıf tahminleri (0 veya 1)
    # y_proba: Olasılık tahminleri (ROC-AUC hesabı için gerekli)
    y_pred = model.predict(X_test)
    y_proba = model.predict_proba(X_test)[:, 1]
    
    # 4. Performans metriklerinin hesaplanması ve kaydedilmesi
    accuracy = accuracy_score(y_test, y_pred)
    f1 = f1_score(y_test, y_pred)
    roc_auc = roc_auc_score(y_test, y_proba)
    
    mlflow.log_metric("accuracy", accuracy)
    mlflow.log_metric("f1_score", f1)
    mlflow.log_metric("roc_auc", roc_auc)
    
    # 5. Sonuçların görüntülenmesi
    print(f"  ✓ Accuracy: {accuracy:.4f}")
    print(f"  ✓ F1-Score: {f1:.4f}")
    print(f"  ✓ ROC AUC: {roc_auc:.4f}")
    
    # 6. Eğitilmiş modelin artifact olarak kaydedilmesi
    # Bu model daha sonra yüklenip kullanılabilir
    mlflow.sklearn.log_model(model, "logistic_regression_model")
    print(f"  ✓ Model MLflow'a kaydedildi")

## Adım 6: Deney 2 - Random Forest (Basit Model)

**Model Seçimi: Random Forest**

Random Forest, ensemble learning (topluluk öğrenmesi) yaklaşımına dayanan güçlü bir algoritmadır. Temel özellikleri:

- **Bagging Mekanizması**: Birden fazla karar ağacının tahminlerini birleştirir
- **Özellik Rastgeleliği**: Her ağaç, özelliklerin rastgele alt kümesini kullanır
- **Overfitting Direnci**: Tek ağaçlara göre daha genelleştirilebilir

**Hiperparametre Konfigürasyonu:**

Bu denemede kasıtlı olarak düşük parametre değerleri kullanılmıştır:
- `n_estimators=10`: Küçük topluluk (hızlı eğitim, düşük performans)
- `max_depth=5`: Sınırlı ağaç derinliği (underfitting riski)

**Amaç**: Bu basit model, sonraki gelişmiş modelle karşılaştırma için bir temel (baseline) oluşturur. Parametre seçiminin model performansı üzerindeki etkisini gösterir.

In [ ]:
with mlflow.start_run(run_name="Random Forest (n=10)"):
    print("🔄 Çalışan Deney: Random Forest (n=10)")
    
    # 1. Hiperparametre tanımlama ve kaydetme
    n_estimators = 10  # Topluluk içindeki ağaç sayısı
    max_depth = 5      # Her ağacın maksimum derinliği
    
    mlflow.log_param("model_type", "RandomForestClassifier")
    mlflow.log_param("n_estimators", n_estimators)
    mlflow.log_param("max_depth", max_depth)
    mlflow.log_param("criterion", "gini")  # Bölme kriteri
    
    # 2. Model oluşturma ve eğitim
    # random_state: Bootstrap örneklemesi için sabit tohum
    model = RandomForestClassifier(
        n_estimators=n_estimators, 
        max_depth=max_depth, 
        random_state=42
    )
    model.fit(X_train, y_train)
    
    # 3. Tahmin aşaması
    y_pred = model.predict(X_test)
    y_proba = model.predict_proba(X_test)[:, 1]
    
    # 4. Metrik hesaplama ve kaydetme
    accuracy = accuracy_score(y_test, y_pred)
    f1 = f1_score(y_test, y_pred)
    roc_auc = roc_auc_score(y_test, y_proba)
    
    mlflow.log_metric("accuracy", accuracy)
    mlflow.log_metric("f1_score", f1)
    mlflow.log_metric("roc_auc", roc_auc)

    # 5. Sonuç raporlama
    print(f"  ✓ Accuracy: {accuracy:.4f}")
    print(f"  ✓ F1-Score: {f1:.4f}")
    print(f"  ✓ ROC AUC: {roc_auc:.4f}")
    
    # 6. Model saklama
    mlflow.sklearn.log_model(model, "random_forest_model")
    print(f"  ✓ Model MLflow'a kaydedildi")

## Adım 7: Deney 3 - Random Forest (Gelişmiş Model)

**Parametre Optimizasyonu:**

Bu denemede, Random Forest modelinin kapasitesi artırılmıştır:
- `n_estimators=100`: Daha büyük topluluk (daha kararlı tahminler)
- `max_depth=10`: Daha derin ağaçlar (daha karmaşık kalıpları öğrenme)

**Beklenen Davranış:**

Parametre artışının olası etkileri:
1. **Performans İyileşmesi**: Daha fazla ağaç ve derinlik, modelin veri setindeki karmaşık ilişkileri öğrenmesine olanak tanır
2. **Eğitim Süresi**: Hesaplama maliyeti artabilir
3. **Overfitting Riski**: Çok yüksek parametreler, test setinde performans düşüşüne yol açabilir

**Model Karşılaştırması:**

MLflow UI kullanarak bu üç modeli karşılaştırırken dikkat edilecek noktalar:
- ROC-AUC skorlarındaki değişim
- Parametre-performans ilişkisi
- Eğitim süresi vs. doğruluk ödünleşmesi (trade-off)

In [ ]:
with mlflow.start_run(run_name="Random Forest (n=100)"):
    print("🔄 Çalışan Deney: Random Forest (n=100)")
    
    # 1. Gelişmiş hiperparametre konfigürasyonu
    n_estimators = 100  # Daha geniş topluluk için ağaç sayısı artırıldı
    max_depth = 10      # Daha karmaşık kalıpları öğrenmek için derinlik artırıldı
    
    mlflow.log_param("model_type", "RandomForestClassifier")
    mlflow.log_param("n_estimators", n_estimators)
    mlflow.log_param("max_depth", max_depth)
    mlflow.log_param("criterion", "gini")
    mlflow.log_param("min_samples_split", 2)  # Varsayılan değer (dokümantasyon için)
    
    # 2. Model eğitimi
    model = RandomForestClassifier(
        n_estimators=n_estimators, 
        max_depth=max_depth, 
        random_state=42
    )
    model.fit(X_train, y_train)
    
    # 3. Tahmin üretimi
    y_pred = model.predict(X_test)
    y_proba = model.predict_proba(X_test)[:, 1]
    
    # 4. Kapsamlı metrik değerlendirmesi
    accuracy = accuracy_score(y_test, y_pred)
    f1 = f1_score(y_test, y_pred)
    roc_auc = roc_auc_score(y_test, y_proba)
    
    mlflow.log_metric("accuracy", accuracy)
    mlflow.log_metric("f1_score", f1)
    mlflow.log_metric("roc_auc", roc_auc)

    # 5. Performans değerlendirmesi
    print(f"  ✓ Accuracy: {accuracy:.4f}")
    print(f"  ✓ F1-Score: {f1:.4f}")
    print(f"  ✓ ROC AUC: {roc_auc:.4f}")
    
    # 6. Model persistance (kalıcı saklama)
    mlflow.sklearn.log_model(model, "random_forest_model")
    print(f"  ✓ Model MLflow'a kaydedildi")

## MLflow UI ile Deneyleri İnceleme

### Tracking Verilerine Erişim

Kod hücreleri çalıştırıldıktan sonra, tüm deney verileri otomatik olarak kaydedilir. Bu veriler iki şekilde erişilebilir:

**1. Dosya Sistemi:**
- Proje kök dizininde `mlruns/` klasörü oluşur
- Her deney için ayrı bir alt dizin
- Parametreler, metrikler ve artifactlar JSON formatında saklanır

**2. MLflow UI (Önerilen):**

MLflow UI, deneyleri görselleştirmek ve karşılaştırmak için web tabanlı bir arayüz sağlar.

**UI'ı Başlatma:**
```bash
mlflow ui --host 127.0.0.1 --port 5000
```

**Tarayıcıda Açma:**
- URL: `http://127.0.0.1:5000`
- Sol panelde "Churn Prediction Experiments" deneyini seçin

### UI Özellikleri

**1. Deney Listesi:**
- Tüm runs kronolojik olarak listelenir
- Her run için tarih, süre ve durum bilgisi görünür

**2. Metrik Karşılaştırma:**
- İlgili runs'ları seçin
- "Compare" butonuna tıklayın
- Paralel koordinat grafikleri ve tablo görünümü kullanılabilir

**3. Model Artifactları:**
- Her run'ın sayfasında "Artifacts" sekmesi
- Kaydedilen modeller indirilebilir veya doğrudan yüklenebilir
- Model signature (input/output şeması) otomatik kaydedilir

**4. Metrik Görselleştirme:**
- Zaman serisi grafikleri (iteratif eğitimlerde)
- Parametre vs. metrik scatter plotları
- En iyi modeli belirlemek için sıralama seçenekleri

## Pratik Alıştırma: Kendi Denemenizi Tasarlayın

Bu bölümde öğrendiklerinizi pekiştirmek için aşağıdaki görevi tamamlayın:

### Görev Tanımı

Yukarıdaki kod yapısını kullanarak dördüncü bir deney ekleyin:

**Önerilen Konfigürasyon:**
- Model: `RandomForestClassifier` veya farklı bir algoritma (örn: `GradientBoostingClassifier`, `SVC`)
- Hiperparametreler: Kendi seçtiğiniz değerler
- Run adı: Modeli ve parametreleri tanımlayan açıklayıcı bir isim

### Değerlendirme Kriterleri

1. **Teknik Uygulama:**
   - Tüm parametreler `mlflow.log_param()` ile kaydedilmiş mi?
   - Üç metrik (accuracy, f1_score, roc_auc) hesaplanıp kaydedilmiş mi?
   - Model artifact olarak saklanmış mı?

2. **Karşılaştırmalı Analiz:**
   - MLflow UI'da yeni denemeyi önceki 3 deneyle karşılaştırın
   - Hangi model en yüksek ROC-AUC değerini verdi?
   - Parametre değişikliklerinin performansa etkisi nasıl?

3. **Bilimsel Yorum:**
   - Sonuçları bir markdown hücresinde yorumlayın
   - Model seçiminizi ve parametre değerlerinizi gerekçelendirin
   - Olası iyileştirme önerilerinizi belirtin

In [ ]:
# Öğrenci Çalışma Alanı: Buraya kendi denemenizi ekleyin

# with mlflow.start_run(run_name="Kendi Modeliniz"):
#     # Kodunuzu buraya yazın
#     pass

## Hafta 4: Özet ve Anahtar Kavramlar

### MLOps Temelleri

**MLOps'un Kapsamı:**
- Geleneksel DevOps'tan farklı olarak, MLOps üç bileşeni birlikte yönetir: **kod**, **model** ve **veri**
- Bu üçlü yapı, makine öğrenmesi sistemlerinin doğası gereği dinamik ve stokastik olmasından kaynaklanır
- Versiyon kontrolü, test stratejileri ve deployment süreçleri bu üç bileşeni göz önünde bulundurmalıdır

### Deney Yönetiminin Önemi

**Tekrarlanabilirlik (Reproducibility):**
- Bilimsel araştırma standartlarına uygun çalışma
- Aynı koşullarda aynı sonuçları elde edebilme garantisi
- Kod, veri ve çevre (environment) versiyonlarının kaydı

**Karşılaştırılabilirlik (Comparability):**
- Farklı modellerin ve hiperparametrelerin objektif değerlendirilmesi
- Zaman içinde performans değişimlerinin izlenmesi
- Ekip içinde bilgi paylaşımının kolaylaştırılması

### MLflow'un Rolü

**Experiment Tracking:**
- Otomatik parametre ve metrik kaydı
- Artifact yönetimi (modeller, grafikler, veri)
- UI üzerinden görselleştirme ve filtreleme

**Model Registry (İleri Konular):**
- Model versiyonlama
- Production'a terfi mekanizması
- Model lineage (soy ağacı) takibi

### En İyi Uygulamalar

1. **İsimlendirme Standartları:**
   - Run adları açıklayıcı ve tutarlı olmalı (örn: "model_parametre1_parametre2")
   - Parametre isimleri kısaltma içermemeli, anlaşılır olmalı

2. **Kapsamlı Kayıt:**
   - Sadece ana hiperparametreleri değil, tüm konfigürasyonu kaydedin
   - Model eğitim süresini metrik olarak loglamayı düşünün
   - Veri seti versiyonunu veya hash değerini parametre olarak ekleyin

3. **Metrik Seçimi:**
   - Problem tipine uygun metrikleri kullanın (sınıflandırma vs. regresyon)
   - Dengesiz sınıflarda accuracy yerine F1-score veya ROC-AUC tercih edin
   - İş hedeflerine uygun custom metrikler tanımlayın

4. **Model Artifactları:**
   - Eğitilmiş modeli her zaman kaydedin
   - Özellik önem değerlerini veya model açıklama grafiklerini artifact olarak ekleyin
   - Preprocessing adımlarını da model ile birlikte saklayın (pipeline kullanımı)

